$$
\def\CC{\bf C}
\def\QQ{\bf Q}
\def\RR{\bf R}
\def\ZZ{\bf Z}
\def\NN{\bf N}
$$
# Nice pictures and interacts with differential equations

Authors  
Thierry Monteil

Copyright  
CC BY-SA 3.0

## Introduction

Let us have a look at differential equations from Ali’s lecture.

To get a list of the various differential equations solvers, you can do:

In [ ]:
desolvers?

## Symbolic solving

To solve a simple differential equation symbolically, you can do:

In [ ]:
desolve?

We can find a symbolic expression for the solutions of Malthus
differential equation:

In [ ]:
var('t, r')
P = function('P')(t)
desolve(diff(P,t) == r*P, dvar=P, ivar=t)

For Verhulst differential equation, we can try:

In [ ]:
var('t, r, K')
P = function('P')(t)
sol = desolve(diff(P,t) == r*P * (1-P/K), dvar=P, ivar=t)
sol

Unfortunately, the solution is implicit, so we can try to make it
explicit by solving it:

In [ ]:
solve(sol, [P])

This is not better, but we can try with using sympy instead of maxima:

In [ ]:
solve(sol, [P], algorithm='sympy')

This is not so bad, unfortunately we get a sympy object not trasformed
back to a Sage object. We should report the bug.

Let us now have a look at Gompertz differential equation:

In [ ]:
var('t, r, K')
P = function('P')(t)
sol = desolve(diff(P,t) == r*P * log(K/P), dvar=P, ivar=t)
sol

Again, the solution is implicit, so that we have to solve it:

In [ ]:
solve(sol, [P])

Allee’s effect:

In [ ]:
var('t, r, K, M')
P = function('P')(t)
sol = desolve(diff(P,t) == r*P*(P - M)*(K-P), dvar=P, ivar=t)
sol

In [ ]:
solve(sol, [P])

In [ ]:
solve(sol, [P], algorithm='sympy')

This is not very explicit either...

Let us now move to systems of equations. The function to solve systems
of differential equations symbolically is via:

In [ ]:
desolve_system?

We can copy/paste an example from the documentation:

In [ ]:
t = var('t')
x = function('x')(t)
y = function('y')(t)
de1 = diff(x,t) + y - 1 == 0
de2 = diff(y,t) - x + 1 == 0
desolve_system([de1, de2], [x,y])

Let us try with the Lotka-Volterra differential equation:

In [ ]:
var('t,a,b,c,d')
x = function('x')(t)
y = function('y')(t)
de1 = diff(x,t) == a*x - b*x*y
de2 = diff(y,t) == -c*y + d*x*y
sol = desolve_system([de1, de2], [x,y], ivar=t)
sol

Apparently, Maxima is returns something to Sage that involves weird
functions such as ilt and some constant.

## Numerical solving

It is probably time to move towards a numerical approach. Also, we know
since Poincaré that there is no much hope to solve systems of
differential equation symbolically in general.

There are various numerical solvers, let us pick the
`desolve_system_rk4` function that implements the 4th order Runge-Kutta
method:

In [ ]:
desolve_system_rk4?

Let us first solve the system with the parameters `a,b,c,d` be equal to
`1,2,1,1` respectively.

In [ ]:
var('t,x,y')
dx = x - 2*x*y
dy = -y + x*y
sol = desolve_system_rk4([dx,dy], [x,y], ics=[0,0.5,2], ivar=t, end_points=30)

The solution is returned as a list ot triple values `[t,x,y]`

In [ ]:
sol[:10]

We can superpose two plots corresponding to the evolution of $x(t)$ and
$y(t)$ :

In [ ]:
line((t,x) for t,x,y in sol) + line(((t,y) for t,x,y in sol), color='red')

Let us add a legend to see which color corresonds to which entity:

We can also look at the 3-dimensional plot of the function $t \mapsto
(x(t),y(t))$ :

In [ ]:
line(((t,x) for t,x,y in sol), legend_label="Prey") + line(((t,y) for t,x,y in sol), color='red', legend_label="Predator")

In [ ]:
line3d((t,x,y) for t,x,y in sol)

We can also look at the 2-dimensional phase space $(x,t)$ :

In [ ]:
line2d(((x,y) for t,x,y in sol), color='green')

The previous plot is not very round, since the default time step is too
large. We see in the documentation of the `desolve_system_rk4` function
that there is a `step` option which defaults to `0.1`, let us reduce it
to `0.05` :

In [ ]:
sol = desolve_system_rk4([dx,dy], [x,y], ics=[0,0.5,2], ivar=t, end_points=30, step=0.05)
line2d(((x,y) for t,x,y in sol), color='green')

It looks better, however, we get a false sense of symmetry between pray
and predator, since the horizontal axis is compressed compared to the
vertical one. Let us add an option to ensure that both axes are at the
same scale:

In [ ]:
line2d(((x,y) for t,x,y in sol), color='green', aspect_ratio=1)

We can add the vector field (with the `plot_vector_field` function)
corresponding to the differential equation to see that the solution is
tangent to it:

In [ ]:
line2d(((x,y) for t,x,y in sol), color='green', aspect_ratio=1) + plot_vector_field((dx,dy), (x,0,4.2), (y,0,2.5))

We can also see some solutions with the `streamline_plot` function:

In [ ]:
streamline_plot((dx,dy), (0,4), (0,4))

Now, if we want to play with parameters interactively, let us put the
previous code in a function, so that we can handle it easily:

In [ ]:
def lk(tmin=0, tmax=30, x0=0.5, y0=2, a=1, b=2, c=1, d=1, step=0.05, color='green'):
    var('t,x,y')
    dx = a*x - b*x*y
    dy = -c*y + d*x*y
    sol = desolve_system_rk4([dx,dy], [x,y], ics=[tmin,x0,y0], ivar=t, end_points=tmax, step=step)
    return line2d(((x,y) for t,x,y in sol), color=color, aspect_ratio=1)

We put default values to the parameters of the function so that we can
call it easily:

In [ ]:
lk()

Let us now make an interact to see how does the solution depends on the
various parameters. You can see some example of interacts used in
various fields on the wiki page <https://wiki.sagemath.org/interact> in
particular the page about differential equations
<https://wiki.sagemath.org/interact/diffeq>

In [ ]:
@interact
def lk_explore(tmin=slider(vmin=0,vmax=10,step_size=0.1,default=0, label="min time"),
               tmax=slider(vmin=0,vmax=50,step_size=0.1,default=30,label="max time"),
               x0=slider(vmin=0,vmax=3,step_size=0.1,default=0.5,label="$x_0$"),
               y0=slider(vmin=0,vmax=3,step_size=0.1,default=2,label="$y_0$"),
               a=slider(vmin=0,vmax=3,step_size=0.1,default=1,label="$a$"),
               b=slider(vmin=0,vmax=3,step_size=0.1,default=2,label="$b$"),
               c=slider(vmin=0,vmax=3,step_size=0.1,default=1,label="$c$"),
               d=slider(vmin=0,vmax=3,step_size=0.1,default=1,label="$d$"),
               step=slider([1,0.5,0.1,0.05,0.01,0.001,0.005,0.0005],default=0.1,label="step")):
    return lk(tmin=tmin, tmax=tmax, x0=x0, y0=y0, a=a, b=b, c=c, d=d, step=step)

As a last example, we can propose to draw various trajectories with
rainbow colors, see:

In [ ]:
rainbow?

In [ ]:
@interact
def lk_explore(n=slider(vmin=0,vmax=20,default=1,label="number of trajectories"),
               a=slider(vmin=0,vmax=3,step_size=0.1,default=1,label="$a$"),
               b=slider(vmin=0,vmax=3,step_size=0.1,default=2,label="$b$"),
               c=slider(vmin=0,vmax=3,step_size=0.1,default=1,label="$c$"),
               d=slider(vmin=0,vmax=3,step_size=0.1,default=1,label="$d$")):
    x0min = 0.1
    x0max = 1
    g = Graphics()
    for i in range(n):
        x0 = y0 = (i * x0min + (n-i)*x0max)/n
        g += lk(tmin=0, tmax=20, x0=x0, y0=y0, a=a, b=b, c=c, d=d, step=0.05, color=rainbow(n)[i])
    return show(g,xmin=0,xmax=4,ymin=0,ymax=4)